# Analysis of the influence of nearby common venues on the square meter price of properties in Medellín City

#### By Santiago Velez

## Table of Contents

<div class="alert alert-block alert-info" style="margin-top: 20px">

<font size = 3>

1. <a href="#item1">Download and prepare the Dataset of properties</a>

2. <a href="#item2">Set the groups of properties with interquartile analysis</a>

3. <a href="#item3">Explore and analyze Q groups of properties in Medellin</a>

4. <a href="#item4">Conclusions</a>
 
</font>
</div>

### Import libraries

In [1]:
# Import libraries
import pandas as pd
import numpy as np

import json # library to handle JSON files
import requests # library to handle requests

from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge geopy --yes
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if the first time you execute
import folium # map rendering library
print('Libraries imported')

Libraries imported


# 1. Download and prepare the Dataset of properties

## 1.1 Import data of properties in Medellin city

In [39]:
import json
with open('Properties_Medellin.geojson') as f:
    data = json.load(f)

Data of properties into Dataframe.

In [40]:
df = pd.json_normalize(data['features'])
df.dropna()
df.head()

type  properties.OBJECTID  properties.CODIGO properties.CBML  \
0  Feature                    1              87443     04130270007   
1  Feature                    2              90581     04130270014   
2  Feature                    3              76837     04130280019   
3  Feature                    4              90836     04130300003   
4  Feature                    5              81000     04130320021   

   properties.TIPO_DE_OFERTA properties.ESTADO  properties.AREA_PRIVADA  \
0                          2                US                       80   
1                          2                NV                       70   
2                          1                US                       87   
3                          2                US                       35   
4                          1                US                       94   

   properties.VALOR_COMERCIAL        properties.FECHA  properties.FUENTE  \
0                      600000  2013/02/21 00:00:00+00                  4   
1                      500000  2013/05/29 00:00:00+00                  4   
2                    90000000  2012/02/22 00:00:00+00                  1   
3                      190000  2013/06/11 00:00:00+00                  1   
4                   100000000  2012/07/06 00:00:00+00                  1   

   properties.VALOR_M2  properties.NOMBRE_FUENTE  properties.USO_OFERTA  \
0               7500.0                        22                      1   
1               7000.0                        22                      3   
2            1034500.0                         3                      1   
3               5500.0                         3                      3   
4            1064000.0                         3                      1   

  geometry.type                     geometry.coordinates  
0         Point  [-75.56013754861222, 6.281362203469805]  
1         Point  [-75.56011991499687, 6.281879337244785]  
2         Point  [-75.55950273469212, 6.281681757236898]  
3         Point  [-75.55881718772693, 6.281325465734376]  
4         Point  [-75.55848773560459, 6.281669343283677]

Rename Columns

In [4]:
df.rename(columns = {
    'properties.CODIGO': 'Property Code',
    'properties.TIPO_DE_OFERTA': 'Offer Type',
    'properties.VALOR_COMERCIAL': 'Comercial Value',
    'properties.VALOR_M2': 'Mt2 Value',
    'geometry.coordinates': 'Coordinates'
}, inplace = True)

df.head()

type  properties.OBJECTID  Property Code properties.CBML  Offer Type  \
0  Feature                    1          87443     04130270007           2   
1  Feature                    2          90581     04130270014           2   
2  Feature                    3          76837     04130280019           1   
3  Feature                    4          90836     04130300003           2   
4  Feature                    5          81000     04130320021           1   

  properties.ESTADO  properties.AREA_PRIVADA  Comercial Value  \
0                US                       80           600000   
1                NV                       70           500000   
2                US                       87         90000000   
3                US                       35           190000   
4                US                       94        100000000   

         properties.FECHA  properties.FUENTE  Mt2 Value  \
0  2013/02/21 00:00:00+00                  4     7500.0   
1  2013/05/29 00:00:00+00                  4     7000.0   
2  2012/02/22 00:00:00+00                  1  1034500.0   
3  2013/06/11 00:00:00+00                  1     5500.0   
4  2012/07/06 00:00:00+00                  1  1064000.0   

   properties.NOMBRE_FUENTE  properties.USO_OFERTA geometry.type  \
0                        22                      1         Point   
1                        22                      3         Point   
2                         3                      1         Point   
3                         3                      3         Point   
4                         3                      1         Point   

                               Coordinates  
0  [-75.56013754861222, 6.281362203469805]  
1  [-75.56011991499687, 6.281879337244785]  
2  [-75.55950273469212, 6.281681757236898]  
3  [-75.55881718772693, 6.281325465734376]  
4  [-75.55848773560459, 6.281669343283677]

In [5]:
FIELDS = ["Property Code", "Offer Type", "Comercial Value", "Mt2 Value", "Coordinates" ]

df_properties = df[FIELDS]
print('Shape of the df: ', df_properties.shape)
df_properties.head()

Shape of the df:  (15725, 5)


Property Code  Offer Type  Comercial Value  Mt2 Value  \
0          87443           2           600000     7500.0   
1          90581           2           500000     7000.0   
2          76837           1         90000000  1034500.0   
3          90836           2           190000     5500.0   
4          81000           1        100000000  1064000.0   

                               Coordinates  
0  [-75.56013754861222, 6.281362203469805]  
1  [-75.56011991499687, 6.281879337244785]  
2  [-75.55950273469212, 6.281681757236898]  
3  [-75.55881718772693, 6.281325465734376]  
4  [-75.55848773560459, 6.281669343283677]

#### Filter properties to work only with properties for sale (Offer type = 1)

In [6]:
df_properties_for_sale = df_properties[ df_properties["Offer Type"] == 1 ].copy()
print('Shape of the df: ', df_properties_for_sale.shape)
df_properties_for_sale.head(10)

Shape of the df:  (6149, 5)


Property Code  Offer Type  Comercial Value  Mt2 Value  \
2           76837           1         90000000  1034500.0   
4           81000           1        100000000  1064000.0   
7           91380           1         25000000   182500.0   
13          81003           1         85000000   552000.0   
16          79042           1         44430000  1234000.0   
17          79043           1         53022000  1233000.0   
18          89701           1        150000000  1128000.0   
21          80991           1        110000000   873000.0   
22          81626           1         95000000  1131000.0   
24          91749           1         70000000  1094000.0   

                                Coordinates  
2   [-75.55950273469212, 6.281681757236898]  
4   [-75.55848773560459, 6.281669343283677]  
7   [-75.55812114476444, 6.281473115285412]  
13  [-75.56071377616377, 6.283044125616279]  
16  [-75.56041420318351, 6.283232305993462]  
17  [-75.56041420318351, 6.283232305993462]  
18  [-75.55928542553175, 6.283084405769118]  
21   [-75.55805687085824, 6.28303369776205]  
22  [-75.55982318923958, 6.270291472838877]  
24   [-75.5608635558844, 6.271340524505576]

## 1.2 Map of properties for sale in Medellin

Set coordinates Medellín Colombian City 

In [7]:
address = 'Medellin, CO'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude

print('The geograpical coordinate of Medellin are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Medellin are 6.2443382, -75.573553.


In [8]:
# create map of Medellin using latitude and longitude values
map_medellin = folium.Map(location=[latitude, longitude], zoom_start=12)

In [9]:
# add markers to map
for index, row in df_properties_for_sale.iterrows():
    code = row['Property Code']
    latitude = (row['Coordinates'])[1]
    longitude = (row['Coordinates'])[0]
    label = folium.Popup(code, parse_html=True)
    folium.CircleMarker(
        [latitude, longitude],
        radius=4,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_medellin)
    
map_medellin

# 2. Set the groups of properties with interquartile analysis

## 2.1 Quartiles Analysis to classify properties strata

Obtain quartiles ranges

In [10]:
qs = df_properties_for_sale['Mt2 Value'].quantile([.25, .5, .75]).values
print('The quartiles of the data for Mt2 Value are: ', qs)

#Function that determine the quartile
def checkQuartile(value, qs):
     return ('Q1' if value <= qs[0] else 'Q2' if value > qs[0] and value <= qs[1] else 'Q3' if value > qs[1] and value <= qs[2]  else 'Q4')
    
df_properties_for_sale['Quartile'] = df_properties_for_sale['Mt2 Value'].map(lambda x: checkQuartile(x, qs))

df_properties_for_sale.head()


The quartiles of the data for Mt2 Value are:  [ 900000. 1412000. 2000000.]


Property Code  Offer Type  Comercial Value  Mt2 Value  \
2           76837           1         90000000  1034500.0   
4           81000           1        100000000  1064000.0   
7           91380           1         25000000   182500.0   
13          81003           1         85000000   552000.0   
16          79042           1         44430000  1234000.0   

                                Coordinates Quartile  
2   [-75.55950273469212, 6.281681757236898]       Q2  
4   [-75.55848773560459, 6.281669343283677]       Q2  
7   [-75.55812114476444, 6.281473115285412]       Q1  
13  [-75.56071377616377, 6.283044125616279]       Q1  
16  [-75.56041420318351, 6.283232305993462]       Q2

#### Create an independent Dataframe for quartiles Q1 ans Q4

In [11]:
df_properties_q1 = df_properties_for_sale[df_properties_for_sale['Quartile'] == 'Q1']
df_properties_q4 = df_properties_for_sale[df_properties_for_sale['Quartile'] == 'Q4']

print('Shape of q1 is: ', df_properties_q1.shape)
print('Shape of q4 is: ', df_properties_q4.shape)

Shape of q1 is:  (1540, 6)
Shape of q4 is:  (1488, 6)


In [12]:
# create map of Medellin using latitude and longitude values
map_properties = folium.Map(location=[latitude, longitude], zoom_start=12)

# add markers to map properties of quartile 4
for index, row in df_properties_q4.iterrows():
    code = row['Property Code']
    latitude = (row['Coordinates'])[1]
    longitude = (row['Coordinates'])[0]
    label = folium.Popup(code, parse_html=True)
    folium.CircleMarker(
        [latitude, longitude],
        radius=4,
        popup=label,
        color='green',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_properties)

# add markers to map properties of quartile 1
for index, row in df_properties_q1.iterrows():
    code = row['Property Code']
    latitude = (row['Coordinates'])[1]
    longitude = (row['Coordinates'])[0]
    label = folium.Popup(code, parse_html=True)
    folium.CircleMarker(
        [latitude, longitude],
        radius=4,
        popup=label,
        color='red',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_properties)
    
map_properties

# 3. Explore and analyze Q groups of properties in Medellin

## 3.1 Venue Analysis of property of each group

### Statistic Sample
#### Select 20 properties  for each quartile Strata (Q1 and Q4)

In [13]:
df_sample_q1 = df_properties_q1.sample(20)
df_sample_q4 = df_properties_q4.sample(20)

### Segmentation and clustering Analysis for each group

#### Set Foursquare

In [14]:
CLIENT_ID = 'GELRBWEO4KWMOQPN5IZISPVSW5XYIS53422E1S1GOFXJFWLV' # Foursquare ID
CLIENT_SECRET = 'F5XFTGXAWEK0YKKV5T4RUSRLLSM23X0B2YCDVOVOMCSKPCAM' # Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # Number of venues to get in a request

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: GELRBWEO4KWMOQPN5IZISPVSW5XYIS53422E1S1GOFXJFWLV
CLIENT_SECRET:F5XFTGXAWEK0YKKV5T4RUSRLLSM23X0B2YCDVOVOMCSKPCAM


#### Get venue for each property in the group

In [15]:
# Function to obtain venues for every property in groups 
def getNearbyVenues(codes, coordinates, radius=200):
    
    venues_list=[]
    for code, coordinate in zip(codes, coordinates):
        print(code)
        lat = coordinate[1]
        lng = coordinate[0]
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            code, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Property Code', 
                  'Property Latitude', 
                  'Property Longitude',  
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [16]:
# Group Q1 properties in Medellin venues
q1_properties_venues = getNearbyVenues(codes=df_sample_q1['Property Code'],
                                   coordinates=df_sample_q1['Coordinates']
                                  )

85774
83797
81592
88111
80607
80619
80594
86053
88252
90729
80331
80374
85148
92215
82132
83024
83765
85207
81013
91129


In [17]:
# Group Q4 properties in Medellin venues
q4_properties_venues = getNearbyVenues(codes=df_sample_q4['Property Code'],
                                   coordinates=df_sample_q4['Coordinates']
                                  )

92137
88215
83905
81458
89666
76784
82545
87686
76701
87984
77550
85335
87775
89737
90575
81037
78943
87833
77857
81182


### Analyze Each Property for each group Q1 and Q4

#### Create a dataframe to relate every property vs. every venue category

In [18]:
# one hot encoding
q1_onehot = pd.get_dummies(q1_properties_venues[['Venue Category']], prefix="", prefix_sep="")
q4_onehot = pd.get_dummies(q4_properties_venues[['Venue Category']], prefix="", prefix_sep="")


# add property Code column back to dataframe
q1_onehot['Property Code'] = q1_properties_venues['Property Code']
q4_onehot['Property Code'] = q4_properties_venues['Property Code'] 


# move property Code column to the first column
fixed_columns_q1 = [q1_onehot.columns[-1]] + list(q1_onehot.columns[:-1])
q1_onehot = q1_onehot[fixed_columns_q1]

fixed_columns_q4 = [q4_onehot.columns[-1]] + list(q4_onehot.columns[:-1])
q4_onehot = q4_onehot[fixed_columns_q4]

print('shape of the Q1 df is: ', q1_onehot.shape)
print('shape of the Q4 df is: ', q4_onehot.shape)
q1_onehot.head()

shape of the Q1 df is:  (18, 18)
shape of the Q4 df is:  (168, 77)


Property Code  Argentinian Restaurant  Bar  Business Service  \
0          83797                       0    0                 0   
1          83797                       0    0                 0   
2          83797                       0    0                 0   
3          80619                       0    1                 0   
4          80619                       0    0                 0   

   Construction & Landscaping  Convenience Store  Dessert Shop  \
0                           0                  0             0   
1                           0                  0             0   
2                           0                  0             0   
3                           0                  0             0   
4                           0                  0             0   

   Fast Food Restaurant  Fish & Chips Shop  Food Court  Hardware Store  \
0                     0                  0           1               0   
1                     0                  0           0               0   
2                     0                  0           0               0   
3                     0                  0           0               0   
4                     0                  1           0               0   

   Motorcycle Shop  Park  Public Art  Scenic Lookout  Seafood Restaurant  \
0                0     0           0               0                   0   
1                0     0           0               0                   1   
2                0     0           0               0                   0   
3                0     0           0               0                   0   
4                0     0           0               0                   0   

   Tourist Information Center  Tram Station  
0                           0             0  
1                           0             0  
2                           0             1  
3                           0             0  
4                           0             0

#### Group rows by property code and by taking the mean of the frequency of occurrence of each category


In [19]:
q1_property_grouped = q1_onehot.groupby('Property Code').mean().reset_index()
q4_property_grouped = q4_onehot.groupby('Property Code').mean().reset_index()

# Let's confirm the new sizes
print('Q1', q1_property_grouped.shape)
print('Q4', q4_property_grouped.shape)

Q1 (10, 18)
Q4 (18, 77)


#### Create a dataframe with the properties and the top 10 venues per property
Function to sort venues in descendent order

In [20]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Dataframes with the property code and the top 10 venues

In [21]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Property Code']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframes for each group
q1_properties_venues_sorted = pd.DataFrame(columns=columns)
q1_properties_venues_sorted['Property Code'] = q1_property_grouped['Property Code']

q4_properties_venues_sorted = pd.DataFrame(columns=columns)
q4_properties_venues_sorted['Property Code'] = q4_property_grouped['Property Code']


for ind in np.arange(q1_property_grouped.shape[0]):
    q1_properties_venues_sorted.iloc[ind, 1:] = return_most_common_venues(q1_property_grouped.iloc[ind, :], num_top_venues)
    
for ind in np.arange(q4_property_grouped.shape[0]):
    q4_properties_venues_sorted.iloc[ind, 1:] = return_most_common_venues(q4_property_grouped.iloc[ind, :], num_top_venues)

    
q1_properties_venues_sorted.head()

Property Code       1st Most Common Venue 2nd Most Common Venue  \
0          80374  Construction & Landscaping          Tram Station   
1          80619           Fish & Chips Shop                   Bar   
2          81013      Argentinian Restaurant     Fish & Chips Shop   
3          82132              Hardware Store          Tram Station   
4          83024             Motorcycle Shop          Tram Station   

  3rd Most Common Venue 4th Most Common Venue       5th Most Common Venue  \
0     Fish & Chips Shop                   Bar            Business Service   
1            Public Art          Dessert Shop                Tram Station   
2                   Bar      Business Service  Construction & Landscaping   
3     Fish & Chips Shop                   Bar            Business Service   
4     Fish & Chips Shop                   Bar            Business Service   

        6th Most Common Venue       7th Most Common Venue  \
0           Convenience Store                Dessert Shop   
1            Business Service  Construction & Landscaping   
2           Convenience Store                Dessert Shop   
3  Construction & Landscaping           Convenience Store   
4  Construction & Landscaping           Convenience Store   

  8th Most Common Venue 9th Most Common Venue      10th Most Common Venue  
0  Fast Food Restaurant            Food Court  Tourist Information Center  
1     Convenience Store  Fast Food Restaurant                  Food Court  
2  Fast Food Restaurant          Tram Station  Tourist Information Center  
3          Dessert Shop  Fast Food Restaurant                  Food Court  
4          Dessert Shop  Fast Food Restaurant                  Food Court

In [22]:
q4_properties_venues_sorted.head()

Property Code 1st Most Common Venue 2nd Most Common Venue  \
0          76701        Clothing Store        Sandwich Place   
1          76784                Bakery           Yoga Studio   
2          77550                  Park    Seafood Restaurant   
3          77857                  Park              Boutique   
4          78943                 Hotel             BBQ Joint   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0             BBQ Joint        Ice Cream Shop                  Café   
1            Eye Doctor  Colombian Restaurant              Creperie   
2           Yoga Studio        Clothing Store           Coffee Shop   
3    Seafood Restaurant                   Bar           Coffee Shop   
4            Eye Doctor  Colombian Restaurant              Creperie   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0           Karaoke Bar    Mexican Restaurant           Men's Store   
1          Cupcake Shop          Dance Studio         Deli / Bodega   
2  Colombian Restaurant              Creperie          Cupcake Shop   
3  Colombian Restaurant              Creperie          Cupcake Shop   
4          Cupcake Shop          Dance Studio         Deli / Bodega   

  9th Most Common Venue 10th Most Common Venue  
0    Chinese Restaurant                 Lounge  
1                 Diner             Donut Shop  
2          Dance Studio          Deli / Bodega  
3          Dance Studio          Deli / Bodega  
4                 Diner             Donut Shop

## 3.2 Cluster Group of Properties

## 3.2.1 Clustering and segmentation for Q1 group

K-means with 5 clusters

In [23]:
# set number of clusters
kclusters = 5

q1_property_grouped_for_clustering = q1_property_grouped.drop('Property Code', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(q1_property_grouped_for_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([3, 1, 4, 0, 1, 1, 1, 2, 1, 2])

#### New dataframe with complete information of property including cluster group

In [24]:
# add clustering labels
q1_properties_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)
q1_properties_venues_sorted = q1_properties_venues_sorted.astype({'Cluster Labels': int})

q1_properties_merged = df_sample_q1

# merge toronto_grouped with toronto data (df) to add latitude/longitude for each neighborhood
q1_properties_merged = q1_properties_merged.join(q1_properties_venues_sorted.set_index('Property Code'), on='Property Code')

q1_properties_merged = q1_properties_merged.dropna()
q1_properties_merged = q1_properties_merged.astype({'Cluster Labels': int})

q1_properties_merged.head()

Property Code  Offer Type  Comercial Value  Mt2 Value  \
3393          83797           1         26950000   350000.0   
1587          80619           1         95000000   772500.0   
1832          86053           1        110000000   709500.0   
3754          80374           1        101881000   893500.0   
1455          85148           1         52726800   712500.0   

                                  Coordinates Quartile  Cluster Labels  \
3393  [-75.55520288649677, 6.241200755152511]       Q1               1   
1587  [-75.57270724106684, 6.291104299740561]       Q1               1   
1832  [-75.58476106705798, 6.283855322877113]       Q1               1   
3754  [-75.55940233917987, 6.237203767377195]       Q1               3   
1455  [-75.57573302158212, 6.287084439615694]       Q1               2   

           1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
3393                Tram Station    Seafood Restaurant            Food Court   
1587           Fish & Chips Shop                   Bar            Public Art   
1832            Business Service     Convenience Store          Tram Station   
3754  Construction & Landscaping          Tram Station     Fish & Chips Shop   
1455        Fast Food Restaurant          Tram Station     Fish & Chips Shop   

     4th Most Common Venue 5th Most Common Venue       6th Most Common Venue  \
3393        Scenic Lookout            Public Art                        Park   
1587          Dessert Shop          Tram Station            Business Service   
1832     Fish & Chips Shop                   Bar  Construction & Landscaping   
3754                   Bar      Business Service           Convenience Store   
1455                   Bar      Business Service  Construction & Landscaping   

           7th Most Common Venue 8th Most Common Venue  \
3393             Motorcycle Shop        Hardware Store   
1587  Construction & Landscaping     Convenience Store   
1832                Dessert Shop  Fast Food Restaurant   
3754                Dessert Shop  Fast Food Restaurant   
1455           Convenience Store          Dessert Shop   

           9th Most Common Venue      10th Most Common Venue  
3393  Tourist Information Center           Fish & Chips Shop  
1587        Fast Food Restaurant                  Food Court  
1832                  Food Court  Tourist Information Center  
3754                  Food Court  Tourist Information Center  
1455                  Food Court  Tourist Information Center

#### Visualization in a map of the result of the clusters

In [25]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for coordinate, poi, cluster in zip(q1_properties_merged['Coordinates'], q1_properties_merged['Property Code'], q1_properties_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    lat = coordinate[1]
    lon = coordinate[0]
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

### 3.2.1.1 Examine Clusters for Q1 group

#### Evaluate and stablish a describing group that distinguish each cluster.

#### Cluster 1

In [26]:
q1_properties_merged.loc[q1_properties_merged['Cluster Labels'] == 0, q1_properties_merged.columns[[1] + list(range(5, q1_properties_merged.shape[1]))]]

Offer Type Quartile  Cluster Labels 1st Most Common Venue  \
1719           1       Q1               0        Hardware Store   

     2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
1719          Tram Station     Fish & Chips Shop                   Bar   

     5th Most Common Venue       6th Most Common Venue 7th Most Common Venue  \
1719      Business Service  Construction & Landscaping     Convenience Store   

     8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
1719          Dessert Shop  Fast Food Restaurant             Food Court

#### Cluster 2

In [27]:
q1_properties_merged.loc[q1_properties_merged['Cluster Labels'] == 1, q1_properties_merged.columns[[1] + list(range(5, q1_properties_merged.shape[1]))]]

Offer Type Quartile  Cluster Labels 1st Most Common Venue  \
3393           1       Q1               1          Tram Station   
1587           1       Q1               1     Fish & Chips Shop   
1832           1       Q1               1      Business Service   
2255           1       Q1               1       Motorcycle Shop   
2404           1       Q1               1        Scenic Lookout   

     2nd Most Common Venue       3rd Most Common Venue 4th Most Common Venue  \
3393    Seafood Restaurant                  Food Court        Scenic Lookout   
1587                   Bar                  Public Art          Dessert Shop   
1832     Convenience Store                Tram Station     Fish & Chips Shop   
2255          Tram Station           Fish & Chips Shop                   Bar   
2404                  Park  Tourist Information Center          Tram Station   

     5th Most Common Venue       6th Most Common Venue  \
3393            Public Art                        Park   
1587          Tram Station            Business Service   
1832                   Bar  Construction & Landscaping   
2255      Business Service  Construction & Landscaping   
2404  Fast Food Restaurant                         Bar   

           7th Most Common Venue       8th Most Common Venue  \
3393             Motorcycle Shop              Hardware Store   
1587  Construction & Landscaping           Convenience Store   
1832                Dessert Shop        Fast Food Restaurant   
2255           Convenience Store                Dessert Shop   
2404            Business Service  Construction & Landscaping   

           9th Most Common Venue      10th Most Common Venue  
3393  Tourist Information Center           Fish & Chips Shop  
1587        Fast Food Restaurant                  Food Court  
1832                  Food Court  Tourist Information Center  
2255        Fast Food Restaurant                  Food Court  
2404           Convenience Store                Dessert Shop

#### Cluster 3

In [28]:
q1_properties_merged.loc[q1_properties_merged['Cluster Labels'] == 2, q1_properties_merged.columns[[1] + list(range(5, q1_properties_merged.shape[1]))]]

Offer Type Quartile  Cluster Labels 1st Most Common Venue  \
1455           1       Q1               2  Fast Food Restaurant   
2813           1       Q1               2  Fast Food Restaurant   

     2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
1455          Tram Station     Fish & Chips Shop                   Bar   
2813          Tram Station     Fish & Chips Shop                   Bar   

     5th Most Common Venue       6th Most Common Venue 7th Most Common Venue  \
1455      Business Service  Construction & Landscaping     Convenience Store   
2813      Business Service  Construction & Landscaping     Convenience Store   

     8th Most Common Venue 9th Most Common Venue      10th Most Common Venue  
1455          Dessert Shop            Food Court  Tourist Information Center  
2813          Dessert Shop            Food Court  Tourist Information Center

#### Cluster 4

In [29]:
q1_properties_merged.loc[q1_properties_merged['Cluster Labels'] == 3, q1_properties_merged.columns[[1] + list(range(5, q1_properties_merged.shape[1]))]]

Offer Type Quartile  Cluster Labels       1st Most Common Venue  \
3754           1       Q1               3  Construction & Landscaping   

     2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
3754          Tram Station     Fish & Chips Shop                   Bar   

     5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
3754      Business Service     Convenience Store          Dessert Shop   

     8th Most Common Venue 9th Most Common Venue      10th Most Common Venue  
3754  Fast Food Restaurant            Food Court  Tourist Information Center

#### Cluster 5

In [30]:
q1_properties_merged.loc[q1_properties_merged['Cluster Labels'] == 4, q1_properties_merged.columns[[1] + list(range(5, q1_properties_merged.shape[1]))]]

Offer Type Quartile  Cluster Labels   1st Most Common Venue  \
747           1       Q1               4  Argentinian Restaurant   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
747     Fish & Chips Shop                   Bar      Business Service   

          5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
747  Construction & Landscaping     Convenience Store          Dessert Shop   

    8th Most Common Venue 9th Most Common Venue      10th Most Common Venue  
747  Fast Food Restaurant          Tram Station  Tourist Information Center

## 3.2.2 Clustering and segmentation for Q4 group

K-means with 5 clusters

In [31]:
# set number of clusters
kclusters = 5

q4_property_grouped_for_clustering = q4_property_grouped.drop('Property Code', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(q4_property_grouped_for_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([1, 2, 4, 4, 1, 1, 1, 1, 0, 1])

#### New dataframe with complete information of property including cluster group

In [32]:
# add clustering labels
q4_properties_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)
q4_properties_venues_sorted = q4_properties_venues_sorted.astype({'Cluster Labels': int})

q4_properties_merged = df_sample_q4

# merge toronto_grouped with toronto data (df) to add latitude/longitude for each neighborhood
q4_properties_merged = q4_properties_merged.join(q4_properties_venues_sorted.set_index('Property Code'), on='Property Code')

# Drop properties without registers of nearby venues
q4_properties_merged = q4_properties_merged.dropna()
q4_properties_merged = q4_properties_merged.astype({'Cluster Labels': int})

q4_properties_merged.head()

Property Code  Offer Type  Comercial Value   Mt2 Value  \
9690           92137           1        145000000   2416500.0   
12038          88215           1        245000000   2952000.0   
5337           83905           1        250000000   2809000.0   
13297          81458           1       4500000000  12162000.0   
13765          89666           1        284000000   3155500.0   

                                   Coordinates Quartile  Cluster Labels  \
9690   [-75.59486612610264, 6.256163067896392]       Q4               3   
12038  [-75.56738836807868, 6.199703603807032]       Q4               1   
5337   [-75.58778454380993, 6.244824265285082]       Q4               1   
13297  [-75.57506804873242, 6.199174703611121]       Q4               1   
13765  [-75.57326695477863, 6.201332388375282]       Q4               1   

      1st Most Common Venue   2nd Most Common Venue 3rd Most Common Venue  \
9690     Athletics & Sports             Yoga Studio            Eye Doctor   
12038                 Hotel  Furniture / Home Store    Italian Restaurant   
5337                  Plaza               BBQ Joint                Bakery   
13297                  Café      Italian Restaurant           Salad Place   
13765                 Hotel                     Bar                  Café   

      4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
9690   Colombian Restaurant              Creperie          Cupcake Shop   
12038           Beer Garden           Yoga Studio            Donut Shop   
5337            Salad Place           Beer Garden                  Café   
13297                 Hotel          Burger Joint  Colombian Restaurant   
13765    Italian Restaurant            Restaurant          Burger Joint   

      7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
9690           Dance Studio         Deli / Bodega                 Diner   
12038  Colombian Restaurant              Creperie          Cupcake Shop   
5337              Nightclub           Yoga Studio         Deli / Bodega   
13297             Bookstore         Shopping Mall        Ice Cream Shop   
13765           Pizza Place        Breakfast Spot         Deli / Bodega   

      10th Most Common Venue  
9690              Donut Shop  
12038           Dance Studio  
5337    Colombian Restaurant  
13297            Supermarket  
13765    Japanese Restaurant

#### Visualization in a map of the result of the clusters

In [33]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for coordinate, poi, cluster in zip(q4_properties_merged['Coordinates'], q4_properties_merged['Property Code'], q4_properties_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    lat = coordinate[1]
    lon = coordinate[0]
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

### 3.2.2.1 Examine Clusters for Q4 group

#### Evaluate and stablish a describing group that distinguish each cluster.

#### Cluster 1

In [34]:
q4_properties_merged.loc[q4_properties_merged['Cluster Labels'] == 0, q4_properties_merged.columns[[1] + list(range(5, q4_properties_merged.shape[1]))]]

Offer Type Quartile  Cluster Labels 1st Most Common Venue  \
5023           1       Q4               0                   Bar   
4393           1       Q4               0                   Bar   

     2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
5023          Soccer Field           Yoga Studio                 Diner   
4393           Yoga Studio            Eye Doctor  Colombian Restaurant   

     5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
5023           Coffee Shop  Colombian Restaurant              Creperie   
4393              Creperie          Cupcake Shop          Dance Studio   

     8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
5023          Cupcake Shop          Dance Studio          Deli / Bodega  
4393         Deli / Bodega                 Diner             Donut Shop

#### Cluster 2

In [35]:
q4_properties_merged.loc[q4_properties_merged['Cluster Labels'] == 1, q4_properties_merged.columns[[1] + list(range(5, q4_properties_merged.shape[1]))]]

Offer Type Quartile  Cluster Labels 1st Most Common Venue  \
12038           1       Q4               1                 Hotel   
5337            1       Q4               1                 Plaza   
13297           1       Q4               1                  Café   
13765           1       Q4               1                 Hotel   
4747            1       Q4               1        Clothing Store   
5250            1       Q4               1            Eye Doctor   
14684           1       Q4               1                 Hotel   
3863            1       Q4               1            Restaurant   
12789           1       Q4               1           Yoga Studio   
7818            1       Q4               1                 Hotel   
5775            1       Q4               1             Wine Shop   
6927            1       Q4               1  Gym / Fitness Center   

        2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
12038  Furniture / Home Store    Italian Restaurant           Beer Garden   
5337                BBQ Joint                Bakery           Salad Place   
13297      Italian Restaurant           Salad Place                 Hotel   
13765                     Bar                  Café    Italian Restaurant   
4747           Sandwich Place             BBQ Joint        Ice Cream Shop   
5250         Business Service            Donut Shop  Colombian Restaurant   
14684              Restaurant            TV Station    Italian Restaurant   
3863                      Bar           Pizza Place           Yoga Studio   
12789                     Spa            Food Truck  Fast Food Restaurant   
7818                BBQ Joint            Eye Doctor  Colombian Restaurant   
5775           Ice Cream Shop         Auto Workshop          Dance Studio   
6927             Intersection                Market   Fried Chicken Joint   

      5th Most Common Venue   6th Most Common Venue 7th Most Common Venue  \
12038           Yoga Studio              Donut Shop  Colombian Restaurant   
5337            Beer Garden                    Café             Nightclub   
13297          Burger Joint    Colombian Restaurant             Bookstore   
13765            Restaurant            Burger Joint           Pizza Place   
4747                   Café             Karaoke Bar    Mexican Restaurant   
5250               Creperie            Cupcake Shop          Dance Studio   
14684        Sandwich Place             Yoga Studio         Deli / Bodega   
3863                  Diner             Coffee Shop  Colombian Restaurant   
12789           Coffee Shop    Colombian Restaurant              Creperie   
7818               Creperie            Cupcake Shop          Dance Studio   
5775             Eye Doctor    Colombian Restaurant              Creperie   
6927                    Gym  Furniture / Home Store     French Restaurant   

      8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
12038              Creperie          Cupcake Shop           Dance Studio  
5337            Yoga Studio         Deli / Bodega   Colombian Restaurant  
13297         Shopping Mall        Ice Cream Shop            Supermarket  
13765        Breakfast Spot         Deli / Bodega    Japanese Restaurant  
4747            Men's Store    Chinese Restaurant                 Lounge  
5250          Deli / Bodega                 Diner            Yoga Studio  
14684           Coffee Shop  Colombian Restaurant               Creperie  
3863               Creperie          Cupcake Shop           Dance Studio  
12789          Cupcake Shop          Dance Studio          Deli / Bodega  
7818          Deli / Bodega                 Diner             Donut Shop  
5775           Cupcake Shop         Deli / Bodega                  Diner  
6927             Food Truck  Fast Food Restaurant             Eye Doctor

#### Cluster 3

In [36]:
q4_properties_merged.loc[q4_properties_merged['Cluster Labels'] == 2, q4_properties_merged.columns[[1] + list(range(5, q4_properties_merged.shape[1]))]]

Offer Type Quartile  Cluster Labels 1st Most Common Venue  \
4517           1       Q4               2                Bakery   

     2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
4517           Yoga Studio            Eye Doctor  Colombian Restaurant   

     5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
4517              Creperie          Cupcake Shop          Dance Studio   

     8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
4517         Deli / Bodega                 Diner             Donut Shop

#### Cluster 4

In [37]:
q4_properties_merged.loc[q4_properties_merged['Cluster Labels'] == 3, q4_properties_merged.columns[[1] + list(range(5, q4_properties_merged.shape[1]))]]

Offer Type Quartile  Cluster Labels 1st Most Common Venue  \
9690           1       Q4               3    Athletics & Sports   

     2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
9690           Yoga Studio            Eye Doctor  Colombian Restaurant   

     5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
9690              Creperie          Cupcake Shop          Dance Studio   

     8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
9690         Deli / Bodega                 Diner             Donut Shop

#### Cluster 5

In [38]:
q4_properties_merged.loc[q4_properties_merged['Cluster Labels'] == 4, q4_properties_merged.columns[[1] + list(range(5, q4_properties_merged.shape[1]))]]

Offer Type Quartile  Cluster Labels 1st Most Common Venue  \
8894           1       Q4               4                  Park   
9386           1       Q4               4                  Park   

     2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
8894    Seafood Restaurant           Yoga Studio        Clothing Store   
9386              Boutique    Seafood Restaurant                   Bar   

     5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
8894           Coffee Shop  Colombian Restaurant              Creperie   
9386           Coffee Shop  Colombian Restaurant              Creperie   

     8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
8894          Cupcake Shop          Dance Studio          Deli / Bodega  
9386          Cupcake Shop          Dance Studio          Deli / Bodega